In [1]:
!pip install gtsam

In [2]:
# pylint: disable=invalid-name, E1101

from __future__ import print_function

import math
import unittest
from functools import reduce

import matplotlib.pyplot as plt
import numpy as np
from numpy import linalg
from mpl_toolkits.mplot3d import Axes3D  # pylint: disable=W0611

import matplotlib.patches as mpatches
import matplotlib.transforms as mtransforms
import mpl_toolkits.mplot3d.axes3d as p3

# Required to do animations in colab
from matplotlib import animation
from IPython.display import HTML

import gtsam
import gtsam.utils.plot as gtsam_plot
from gtsam import Pose2

import scipy
from scipy import linalg, matrix

from sympy import Matrix

# Set plot parameters
plt.style.use('ggplot')
plt.rcParams['figure.figsize'] = (8.0, 8.0)
plt.rc('animation', html='jshtml') # needed for animations!
arrowOptions = dict(head_width=.02,head_length=.02, width=0.01)

In [3]:
# Some utility functions for Pose2
def vector3(x, y, z):
    """Create 3D double numpy array."""
    return np.array([x, y, z], dtype=np.float)


def compose(*poses):
    """Compose all Pose2 transforms given as arguments from left to right."""
    return reduce((lambda x, y: x.compose(y)), poses)


def vee(M):
    """Pose2 vee operator."""
    return vector3(M[0, 2], M[1, 2], M[1, 0])


def delta(g0, g1):
    """Difference between x,y,,theta components of SE(2) poses."""
    return vector3(g1.x() - g0.x(), g1.y() - g0.y(), g1.theta() - g0.theta())


def trajectory(g0, g1, N=20):
    """ Create an interpolated trajectory in SE(2), treating x,y, and theta separately.
        g0 and g1 are the initial and final pose, respectively.
        N is the number of *intervals*
        Returns N+1 poses
    """
    e = delta(g0, g1)
    return [Pose2(g0.x()+e[0]*t, g0.y()+e[1]*t, g0.theta()+e[2]*t) for t in np.linspace(0, 1, N)]

# Question 1: Implementation of the Jacobian for the MM

In [14]:
class FourLinkMM(object):
    """Three-link arm class."""

    def __init__(self):
        self.x_b = 0
        self.y_b = 0
        self.theta_b =0
        
        self.L1 = 3.5
        self.L2 = 3.5
        self.L3 = 2.5
        self.L4 = 0.5


    
    def jacobian(self, q):
        """ Calculate manipulator Jacobian.
            Takes numpy array of joint angles, in radians.
        """        
        
        alpha = self.theta_b + q[0]
        beta = self.theta_b + q[0] + q[1]
        gamma = self.theta_b + q[0] + q[1] + q[2]
        delta = self.theta_b + q[0] + q[1] + q[2] + q[3]
        
        j12 = -(self.L1*np.sin(alpha) + self.L2*np.sin(beta) + self.L3*np.sin(gamma) + self.L4*np.sin(delta))
        j13 = -(self.L1*np.sin(alpha) + self.L2*np.sin(beta) + self.L3*np.sin(gamma) + self.L4*np.sin(delta))
        j14 = -(self.L2*np.sin(beta) + self.L3*np.sin(gamma) + self.L4*np.sin(delta))
        j15 = -(self.L3*np.sin(gamma) + self.L4*np.sin(delta))
        j16 = -(self.L4*np.sin(delta))
        
        j02 = -(self.L1*np.cos(alpha) + self.L2*np.cos(beta) + self.L3*np.cos(gamma) + self.L4*np.cos(delta))
        j03 = -(self.L1*np.cos(alpha) + self.L2*np.cos(beta) + self.L3*np.cos(gamma) + self.L4*np.cos(delta))
        j04 = -(self.L2*np.cos(beta) + self.L3*np.cos(gamma) + self.L4*np.cos(delta))
        j05 = -(self.L3*np.cos(gamma) + self.L4*np.cos(delta))
        j06 = -(self.L4*np.cos(delta))
        
        Jacobian = np.array([[1, 0, j02, j03, j04, j05, j06 ], [ 0, 1, j12, j13, j14, j15, j16], [0, 0, 1,1,1,1,1]])
        
        return Jacobian

    def Velocity_in_NullSpace(self, J, u):
      """ Given a velocity of the base (u) and the Jacobian (J). Compute the velocity of the manipulator, thus the end-effector stays in place.
      """
     #TODO fix this function
      J_b = J[:,:3]
      r_b = np.dot(J_b,u)
      J_inv = Matrix.pinv(J)
      q_d = J_inv.dot(-r_b)
      return q_d[-4:]

    def  null_space_projector(self, J):
      """ Compute the null space projector
      """
      I = Matrix.eye(7)
      return I
    
    def null_space_m(self, N):
      """ Modify the null space projector, so it give us the required linear and angular velocity
      """
      return N


# Unittest

In [15]:
# Create common example configurations.
Q0 = np.radians(np.array([0,0,0,0], dtype=np.float))
Q1 = np.radians(np.array([-90,90,0,90], dtype=np.float))
Q2 = np.radians(np.array([-90, 90, 90,90], dtype=np.float))

class TestMMJacobian(unittest.TestCase):
    """Unit tests for functions used below."""

    def setUp(self):
        self.MM = FourLinkMM()

        
    # @unittest.skip("Skipping Jacobian")
    def test_jacobian(self):
        """Test Jacobian calculation."""
        # at rest
        expected = np.array([[1, 0, -10, -10, -6.5, -3,-0.5], [0, 1, 0, 0, 0, 0, 0], [0, 0, 1, 1, 1, 1, 1]], np.float)
        J = self.MM.jacobian(Q0)
        np.testing.assert_array_almost_equal(J, expected)

        # at -90, 90, 0
        expected = np.array([[1, 0, -6.0, -6.0, -6.0, -2.5, 0], [0, 1, 3.0, 3.0, -0.5, -0.5, -0.5], [0, 0, 1, 1, 1, 1, 1]], np.float)
        J = self.MM.jacobian(Q1)
        #print(J)
        #print(expected)
        np.testing.assert_array_almost_equal(J, expected)

    # @unittest.skip("Skipping Complete NullSpace")
    def test_velocity_in_nullSpace(self):
        """Test Velocity_in_NullSpace."""
        v = 1
        w = 0.3
        dt = 0.1

        # at rest        
        expected = Matrix([[-0.0300000000000000], [0.0174311926605505], [-0.00183486238532109], [-0.0155963302752294]])
        J = Matrix(self.MM.jacobian(Q1))
        # This is the current input for the base
        u = Matrix(3,1,[v*np.cos(self.MM.theta_b)*dt,v*np.sin(self.MM.theta_b)*dt,w*dt])
        q_d = self.MM.Velocity_in_NullSpace(J, u)
        print(q_d)
        np.testing.assert_array_almost_equal(q_d, expected)

        # at -90, 90, 0
        expected = Matrix([[-0.0133494208494209], [0.0119208494208494], [-0.00526061776061778], [-0.0233108108108109]])
        self.MM.theta_b = np.radians(45)
        J = Matrix(self.MM.jacobian(Q2))
        u = Matrix(3,1,[v*np.cos(self.MM.theta_b)*dt,v*np.sin(self.MM.theta_b)*dt,w*dt])
        q_d = self.MM.Velocity_in_NullSpace(J, u)
        np.testing.assert_array_almost_equal(q_d, expected)

if __name__ == '__main__':
  unittest.main(argv=['first-arg-is-ignored'], exit=False)


./home/carter/miniconda2/envs/deep_learning/lib/python3.6/site-packages/sympy/matrices/matrices.py:3078: SymPyDeprecationWarning: 

Dot product of non row/column vectors has been deprecated since SymPy
1.2. Use * to take matrix products instead. See
https://github.com/sympy/sympy/issues/13815 for more info.

  useinstead="* to take matrix products").warn()
F

[-0.00483463812110561, -0.00810832401342067, -0.0138416679980828, -0.0138416679980828, 0.0145374660488896, -0.00238376737498003, -0.0144703626777441]



FAIL: test_velocity_in_nullSpace (__main__.TestMMJacobian)
Test Velocity_in_NullSpace.
----------------------------------------------------------------------
Traceback (most recent call last):
  File "<ipython-input-15-6b4a046d706d>", line 42, in test_velocity_in_nullSpace
    np.testing.assert_array_almost_equal(q_d, expected)
  File "/home/carter/miniconda2/envs/deep_learning/lib/python3.6/site-packages/numpy/testing/_private/utils.py", line 1047, in assert_array_almost_equal
    precision=decimal)
  File "/home/carter/miniconda2/envs/deep_learning/lib/python3.6/site-packages/numpy/testing/_private/utils.py", line 765, in assert_array_compare
    raise AssertionError(msg)
AssertionError: 
Arrays are not almost equal to 6 decimals

(shapes (7,), (4, 1) mismatch)
 x: array([-0.00483463812110561, -0.00810832401342067, -0.0138416679980828,
       -0.0138416679980828, 0.0145374660488896, -0.00238376737498003,
       -0.0144703626777441], dtype=object)
 y: array([[-0.0300000000000000],
  

# Question 2: Motion in the Null Space

In [6]:
# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()
N=206
size=10.5
ax.set_xlim((-size, size))
ax.set_ylim((-size, size))
omega = 2*math.pi/N

MM = FourLinkMM()
MM_aux = FourLinkMM()

q = np.radians(np.array([-90, 90, 90,90], dtype=np.float))
len_b = 2
d = np.sqrt(2*len_b*len_b/4)

def init():
  # For animation
  rect = rect = mpatches.Rectangle([MM.x_b-d*np.cos(MM.theta_b+np.radians(45)),MM.y_b-d*np.sin(MM.theta_b+np.radians(45))], len_b, len_b, angle = MM.theta_b*180/np.pi)
  ax.add_artist(mpatches.FancyArrow(MM.x_b,MM.y_b, 1.5*np.cos(MM.theta_b), 1.5*np.sin(MM.theta_b), color='r',head_width = 0.3))
  return (rect,)

def animate(i):
  global pose
  global MM
  global q

  # we set the velocity of the base
  v = 1
  w = 0.3
  dt = 0.1

  # We get the current Jacobian 
  J = Matrix(MM.jacobian(q))
  
  # This is the current input for the base
  u = Matrix(3,1,[v*np.cos(MM.theta_b)*dt,v*np.sin(MM.theta_b)*dt,w*dt])
  
  # ------------------- QUESTION 2 ---------------------

  q_d = MM.Velocity_in_NullSpace(J, u)

  # ----------------------------------------------------
  #  Null space projection
  I = Matrix.eye(7)
  Null = I-J.pinv()*J
  proj = MM.null_space_m(Null)*Matrix(7,1,[u[0],u[1],u[2],0,0,0,0])
  # q_d = proj[3:7]
  # print(proj)
  
  # u = Matrix(3,1,[v*np.cos(MM.theta_b)*dt,v*np.sin(MM.theta_b)*dt,w*dt])
  # sol = N1*x
  # q_d = N2.pinv()*(-sol)
  # # aux = Matrix(7,1,[x[0],x[1],x[2],q_d[0],q_d[1],q_d[2],q_d[3]])
  # aux = Matrix(7,1,[x[0],x[1],x[2],0,0,0,0])
  # q_d = Matrix(4,1,[aux[3],aux[4],aux[5],aux[6]])
  # print(N*aux) 
  # # print(q_d)
  
  # Update the state of the robot with the given velocities.
  MM.x_b = MM.x_b + np.cos(MM.theta_b)*v*dt
  MM.y_b = MM.y_b + np.sin(MM.theta_b)*v*dt
  MM.theta_b = MM.theta_b + w*dt
  q += np.array([q_d[0], q_d[1], q_d[2], q_d[3]], dtype=np.float)



  # ------------------------- ANIMATION ----------------------------------------------------
  MM_aux.x_b = MM_aux.x_b + np.cos(MM_aux.theta_b)*v*dt
  MM_aux.y_b = MM_aux.y_b + np.sin(MM_aux.theta_b)*v*dt
  MM_aux.theta_b = MM_aux.theta_b + w*dt

  rect = mpatches.Rectangle([MM_aux.x_b-d*np.cos(MM_aux.theta_b+np.radians(45)),MM_aux.y_b-d*np.sin(MM_aux.theta_b+np.radians(45))], len_b, len_b, angle = MM_aux.theta_b*180/np.pi, color = 'r', alpha=0.4)
  ax.clear()
  ax.set_xlim((-size, size))
  ax.set_ylim((-size, size))
  ax.add_artist(rect)
  rect = mpatches.Rectangle([MM.x_b-d*np.cos(MM.theta_b+np.radians(45)),MM.y_b-d*np.sin(MM.theta_b+np.radians(45))], len_b, len_b, angle = MM.theta_b*180/np.pi)
  ax.add_artist(rect)
  
  sXl1 = Pose2(0, 0, math.radians(90)+MM.theta_b)
  l1Zl1 = Pose2(0, 0, q[0])
  l1Xl2 = Pose2(MM.L1, 0, 0)
  sTl2 = compose(sXl1, l1Zl1, l1Xl2)
  t1 = sTl2.translation()
  ax.add_artist(mpatches.Rectangle([MM.x_b,MM.y_b], 3.5, 0.1, angle =(MM.theta_b+q[0])*180/np.pi+90, color='r'))
  ax.add_artist(mpatches.FancyArrow(MM.x_b,MM.y_b, 1.5*np.cos(MM.theta_b), 1.5*np.sin(MM.theta_b), color='r',head_width = 0.3))

  l2Zl2 = Pose2(0, 0, q[1])
  l2Xl3 = Pose2(MM.L2, 0, 0)
  sTl3 = compose(sTl2, l2Zl2, l2Xl3)
  t2 = sTl3.translation()
  ax.add_artist(mpatches.Rectangle([t1.x()+MM.x_b,t1.y()+MM.y_b], 3.5, 0.1, angle =(MM.theta_b+q[0]+q[1])*180/np.pi+90, color='g'))

  l3Zl3 = Pose2(0, 0, q[2])
  l3X4 = Pose2(MM.L3, 0, 0)
  sTl4 = compose(sTl3, l3Zl3, l3X4)
  t3 = sTl4.translation()
  ax.add_artist(mpatches.Rectangle([t2.x()+MM.x_b,t2.y()+MM.y_b], 2.5, 0.1, angle =(MM.theta_b+q[0]+q[1]+q[2])*180/np.pi+90, color='b'))

  l4Zl4 = Pose2(0, 0, q[3])
  l4Xt = Pose2(MM.L4, 0, 0)
  sTt = compose(sTl4, l4Zl4, l4Xt)
  t4 = sTt.translation()
  ax.add_artist(mpatches.Rectangle([t3.x()+MM.x_b,t3.y()+MM.y_b], 0.5, 0.1, angle =(MM.theta_b+q[0]+q[1]+q[2]+q[3])*180/np.pi+90, color='k'))

animation.FuncAnimation(fig, animate, init_func=init, 
                        frames=N, interval=100, blit=False)



(3, 3)
u Matrix([[0.100000000000000], [0.0], [0.0300000000000000]])
[[0.0100000000000000]
 [0.0300000000000000]
 [0.0300000000000000]]


IndexError: index 3 is out of bounds for axis 0 with size 3

# Question 3: Null Space Projection


In [7]:
# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()
N=206
size=10.5
ax.set_xlim((-size, size))
ax.set_ylim((-size, size))
omega = 2*math.pi/N

MM = FourLinkMM()
MM_aux = FourLinkMM()
q = np.radians(np.array([-90, 90, 90,90], dtype=np.float))
len_b = 2
d = np.sqrt(2*len_b*len_b/4)

def init():
  # For animation
  rect = rect = mpatches.Rectangle([MM.x_b-d*np.cos(MM.theta_b+np.radians(45)),MM.y_b-d*np.sin(MM.theta_b+np.radians(45))], len_b, len_b, angle = MM.theta_b*180/np.pi)
  ax.add_artist(mpatches.FancyArrow(MM.x_b,MM.y_b, 1.5*np.cos(MM.theta_b), 1.5*np.sin(MM.theta_b), color='r',head_width = 0.3))
  return (rect,)

def animate(i):
  global pose
  global MM
  global MM_aux
  global q

  # we set the velocity of the base
  v = 1
  w = 0.3
  dt = 0.1

  # We get the current Jacobian 
  J = Matrix(MM.jacobian(q))
  
  # This is the current input for the base
  u = Matrix(3,1,[v*np.cos(MM.theta_b)*dt,v*np.sin(MM.theta_b)*dt,w*dt])
  
  # ------------------- QUESTION 3 ---------------------
  #  Null space projection
  I = Matrix.eye(7)
  Null = MM.null_space_projector(J)
  proj = Null*Matrix(7,1,[u[0],u[1],u[2],0,0,0,0])
  #proj = MM.null_space_m(Null)*Matrix(7,1,[u[0],u[1],u[2],0,0,0,0])
  q_d = proj[3:7]
  # print(proj)
  # ----------------------------------------------------
  
  
  # Update the state of the robot with the given velocities.
  MM.x_b = MM.x_b + proj[0]
  MM.y_b = MM.y_b + proj[1]
  MM.theta_b = MM.theta_b + float(proj[2])
  
  MM_aux.x_b = MM_aux.x_b + np.cos(MM_aux.theta_b)*v*dt
  MM_aux.y_b = MM_aux.y_b + np.sin(MM_aux.theta_b)*v*dt
  MM_aux.theta_b = MM_aux.theta_b + w*dt

  q += np.array([q_d[0], q_d[1], q_d[2], q_d[3]], dtype=np.float)

  # ------------------------- ANIMATION ----------------------------------------------------
  rect = mpatches.Rectangle([MM_aux.x_b-d*np.cos(MM_aux.theta_b+np.radians(45)),MM_aux.y_b-d*np.sin(MM_aux.theta_b+np.radians(45))], len_b, len_b, angle = MM_aux.theta_b*180/np.pi, color = 'r', alpha=0.3)
  ax.clear()
  ax.set_xlim((-size, size))
  ax.set_ylim((-size, size))
  ax.add_artist(rect)
  rect = mpatches.Rectangle([MM.x_b-d*np.cos(MM.theta_b+np.radians(45)),MM.y_b-d*np.sin(MM.theta_b+np.radians(45))], len_b, len_b, angle = MM.theta_b*180/np.pi)
  ax.add_artist(rect)
  
  sXl1 = Pose2(0, 0, math.radians(90)+MM.theta_b)
  l1Zl1 = Pose2(0, 0, q[0])
  l1Xl2 = Pose2(MM.L1, 0, 0)
  sTl2 = compose(sXl1, l1Zl1, l1Xl2)
  t1 = sTl2.translation()
  ax.add_artist(mpatches.Rectangle([MM.x_b,MM.y_b], 3.5, 0.1, angle =(MM.theta_b+q[0])*180/np.pi+90, color='r'))
  ax.add_artist(mpatches.FancyArrow(MM.x_b,MM.y_b, 1.5*np.cos(MM.theta_b), 1.5*np.sin(MM.theta_b), color='r',head_width = 0.3))

  l2Zl2 = Pose2(0, 0, q[1])
  l2Xl3 = Pose2(MM.L2, 0, 0)
  sTl3 = compose(sTl2, l2Zl2, l2Xl3)
  t2 = sTl3.translation()
  ax.add_artist(mpatches.Rectangle([t1.x()+MM.x_b,t1.y()+MM.y_b], 3.5, 0.1, angle =(MM.theta_b+q[0]+q[1])*180/np.pi+90, color='g'))

  l3Zl3 = Pose2(0, 0, q[2])
  l3X4 = Pose2(MM.L3, 0, 0)
  sTl4 = compose(sTl3, l3Zl3, l3X4)
  t3 = sTl4.translation()
  ax.add_artist(mpatches.Rectangle([t2.x()+MM.x_b,t2.y()+MM.y_b], 2.5, 0.1, angle =(MM.theta_b+q[0]+q[1]+q[2])*180/np.pi+90, color='b'))

  l4Zl4 = Pose2(0, 0, q[3])
  l4Xt = Pose2(MM.L4, 0, 0)
  sTt = compose(sTl4, l4Zl4, l4Xt)
  t4 = sTt.translation()
  ax.add_artist(mpatches.Rectangle([t3.x()+MM.x_b,t3.y()+MM.y_b], 0.5, 0.1, angle =(MM.theta_b+q[0]+q[1]+q[2]+q[3])*180/np.pi+90, color='k'))

animation.FuncAnimation(fig, animate, init_func=init, 
                        frames=N, interval=100, blit=False)


# Bonus Question: Modified Null Space projection

In [8]:
# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()
N=206
size=10.5
ax.set_xlim((-size, size))
ax.set_ylim((-size, size))
omega = 2*math.pi/N

MM = FourLinkMM()
MM_aux = FourLinkMM()
q = np.radians(np.array([-90, 90, 90,90], dtype=np.float))
len_b = 2
d = np.sqrt(2*len_b*len_b/4)

def init():
  # For animation
  rect = rect = mpatches.Rectangle([MM.x_b-d*np.cos(MM.theta_b+np.radians(45)),MM.y_b-d*np.sin(MM.theta_b+np.radians(45))], len_b, len_b, angle = MM.theta_b*180/np.pi)
  ax.add_artist(mpatches.FancyArrow(MM.x_b,MM.y_b, 1.5*np.cos(MM.theta_b), 1.5*np.sin(MM.theta_b), color='r',head_width = 0.3))
  return (rect,)

def animate(i):
  global pose
  global MM
  global MM_aux
  global q

  # we set the velocity of the base
  v = 1
  w = 0.3
  dt = 0.1

  # We get the current Jacobian 
  J = Matrix(MM.jacobian(q))
  
  # This is the current input for the base
  u = Matrix(3,1,[v*np.cos(MM.theta_b)*dt,v*np.sin(MM.theta_b)*dt,w*dt])
  
  # ------------------- QUESTION 4: Bonus ---------------------
  #  Modified Null space projection
  I = Matrix.eye(7)
  Null = MM.null_space_projector(J)
  proj = MM.null_space_m(Null)*Matrix(7,1,[u[0],u[1],u[2],0,0,0,0])
  q_d = proj[3:7]
  # print(proj)
  # ----------------------------------------------------
  
  
  # Update the state of the robot with the given velocities.
  MM.x_b = MM.x_b + proj[0]
  MM.y_b = MM.y_b + proj[1]
  MM.theta_b = MM.theta_b + float(proj[2])
  
  MM_aux.x_b = MM_aux.x_b + np.cos(MM_aux.theta_b)*v*dt
  MM_aux.y_b = MM_aux.y_b + np.sin(MM_aux.theta_b)*v*dt
  MM_aux.theta_b = MM_aux.theta_b + w*dt

  q += np.array([q_d[0], q_d[1], q_d[2], q_d[3]], dtype=np.float)

  # ------------------------- ANIMATION ----------------------------------------------------
  rect = mpatches.Rectangle([MM_aux.x_b-d*np.cos(MM_aux.theta_b+np.radians(45)),MM_aux.y_b-d*np.sin(MM_aux.theta_b+np.radians(45))], len_b, len_b, angle = MM_aux.theta_b*180/np.pi, color = 'r', alpha=0.3)
  ax.clear()
  ax.set_xlim((-size, size))
  ax.set_ylim((-size, size))
  ax.add_artist(rect)
  rect = mpatches.Rectangle([MM.x_b-d*np.cos(MM.theta_b+np.radians(45)),MM.y_b-d*np.sin(MM.theta_b+np.radians(45))], len_b, len_b, angle = MM.theta_b*180/np.pi)
  ax.add_artist(rect)
  
  sXl1 = Pose2(0, 0, math.radians(90)+MM.theta_b)
  l1Zl1 = Pose2(0, 0, q[0])
  l1Xl2 = Pose2(MM.L1, 0, 0)
  sTl2 = compose(sXl1, l1Zl1, l1Xl2)
  t1 = sTl2.translation()
  ax.add_artist(mpatches.Rectangle([MM.x_b,MM.y_b], 3.5, 0.1, angle =(MM.theta_b+q[0])*180/np.pi+90, color='r'))
  ax.add_artist(mpatches.FancyArrow(MM.x_b,MM.y_b, 1.5*np.cos(MM.theta_b), 1.5*np.sin(MM.theta_b), color='r',head_width = 0.3))

  l2Zl2 = Pose2(0, 0, q[1])
  l2Xl3 = Pose2(MM.L2, 0, 0)
  sTl3 = compose(sTl2, l2Zl2, l2Xl3)
  t2 = sTl3.translation()
  ax.add_artist(mpatches.Rectangle([t1.x()+MM.x_b,t1.y()+MM.y_b], 3.5, 0.1, angle =(MM.theta_b+q[0]+q[1])*180/np.pi+90, color='g'))

  l3Zl3 = Pose2(0, 0, q[2])
  l3X4 = Pose2(MM.L3, 0, 0)
  sTl4 = compose(sTl3, l3Zl3, l3X4)
  t3 = sTl4.translation()
  ax.add_artist(mpatches.Rectangle([t2.x()+MM.x_b,t2.y()+MM.y_b], 2.5, 0.1, angle =(MM.theta_b+q[0]+q[1]+q[2])*180/np.pi+90, color='b'))

  l4Zl4 = Pose2(0, 0, q[3])
  l4Xt = Pose2(MM.L4, 0, 0)
  sTt = compose(sTl4, l4Zl4, l4Xt)
  t4 = sTt.translation()
  ax.add_artist(mpatches.Rectangle([t3.x()+MM.x_b,t3.y()+MM.y_b], 0.5, 0.1, angle =(MM.theta_b+q[0]+q[1]+q[2]+q[3])*180/np.pi+90, color='k'))

animation.FuncAnimation(fig, animate, init_func=init, 
                        frames=N, interval=100, blit=False)